<a href="https://colab.research.google.com/github/ansh-pachauri/GenAI-project-on-collab/blob/main/whisper_small.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
!pip install -U transformers
!pip install -q langchain-community faiss-cpu langchain-google-genai
from datasets import load_dataset
!pip install torch torchaudio torchcodec

## Local Inference on GPU
Model page: https://huggingface.co/openai/whisper-small

⚠️ If the generated code snippets do not work, please open an issue on either the [model repo](https://huggingface.co/openai/whisper-small)
			and/or on [huggingface.js](https://github.com/huggingface/huggingface.js/blob/main/packages/tasks/src/model-libraries-snippets.ts) 🙏

In [2]:
# Use a pipeline as a high-level helper
from transformers import pipeline

pipe = pipeline("automatic-speech-recognition", model="openai/whisper-small")

/usr/local/lib/python3.12/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


Fetching 1 files:   0%|          | 0/1 [00:00<?, ?it/s]

Device set to use cuda:0


In [3]:
# Load model directly
from transformers import AutoProcessor, AutoModelForSpeechSeq2Seq

processor = AutoProcessor.from_pretrained("openai/whisper-small")
model = AutoModelForSpeechSeq2Seq.from_pretrained("openai/whisper-small")

Fetching 1 files:   0%|          | 0/1 [00:00<?, ?it/s]

Fetching 1 files:   0%|          | 0/1 [00:00<?, ?it/s]

In [4]:
from datasets import Audio
import librosa

In [5]:
ds = load_dataset("hf-internal-testing/librispeech_asr_dummy", "clean", split="validation")

In [6]:
ds = ds.cast_column("audio", Audio(decode=False))

In [7]:
sample = ds["audio"]

In [8]:
print(sample)

Column([{'bytes': b'fLaC\x00\x00\x00"\x10\x00\x10\x00\x00\x08:\x00\x18x\x03\xe8\x00\xf0\x00\x01m\xf0\x84\xd1,\x1b\xc02I3e\xbe\x02\xd0\x98\xcf\t\xc4\x03\x00\x00\x12\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x10\x00\x04\x00\x00( \x00\x00\x00reference libFLAC 1.2.1 20070917\x00\x00\x00\x00\x81\x00 \x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x

In [22]:
transcriptions = []
for i in range(2):
    sample = ds[i]["audio"]
    audio_bytes = sample["bytes"]

    # Save the audio to a temporary file
    with open(f"temp_{i}.flac", "wb") as f:
        f.write(audio_bytes)


In [23]:
array, sr = librosa.load(f"temp_{i}.flac", sr=16000)
print(array.shape, sr)

(77040,) 16000


In [24]:
# Process and transcribe
input_features = processor(array, sampling_rate=sr, return_tensors="pt").input_features

In [25]:
predicted_ids = model.generate(input_features)

In [27]:
transcription = processor.batch_decode(predicted_ids, skip_special_tokens=True)

transcriptions.append(transcription[0]) # Append the first element as batch_decode returns a list

print(transcriptions)

[" Nor is Mr. Quilter's manner less interesting than his matter.", " Nor is Mr. Quilter's manner less interesting than his matter."]
